In [1]:
%load_ext autoreload
%autoreload 2
%matplotlib inline

In [2]:
import random
from article_recommendation import ArticleRecommendation

In [3]:
import os
import gc
import pickle
import pandas as pd
import json
import numpy as np
import seaborn as sns
from matplotlib import pyplot as plt

from pyspark import SparkConf, SparkContext
from pyspark.sql import SparkSession
from pyspark.sql.functions import udf, col, transform
from pyspark.sql.types import BooleanType, IntegerType, ArrayType, StringType

In [4]:
import gensim
from gensim.similarities.docsim import MatrixSimilarity
from gensim.corpora import Dictionary
from gensim.models import LdaModel, CoherenceModel
from gensim.parsing.preprocessing import STOPWORDS
from gensim.test.utils import datapath
from gensim import corpora, models
from nltk.stem import WordNetLemmatizer, SnowballStemmer
import nltk
from nltk.stem.porter import *
nltk.download('wordnet')

[nltk_data] Downloading package wordnet to /home/denis/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


True

In [5]:
import warnings
import multiprocessing
from contextlib import closing
warnings.filterwarnings("ignore")

In [6]:
import logging
logging.basicConfig(format='%(asctime)s : %(levelname)s : %(message)s', level=logging.INFO)

In [7]:
spark = SparkSession \
        .builder \
        .master('local[*]') \
        .appName("PySpark for dblpv13") \
        .config("spark.driver.memory", "18g") \
        .config("spark.executor.memory", "18g") \
        .config("spark.driver.maxResultSize", "9g") \
        .getOrCreate()

In [8]:
tt = spark.read.parquet("fin_articles.parquet")

In [18]:
RESULT_FOLDER = '/home/denis/dshibitov/courses/made/project_1/results/lda_model_3'

In [19]:
stemmer = SnowballStemmer(language='english')
def lemmatize_stemming(text):
    return stemmer.stem(WordNetLemmatizer().lemmatize(text, pos='v'))

def preprocess(text):
    result = []
    for token in gensim.utils.simple_preprocess(text):
        if token not in gensim.parsing.preprocessing.STOPWORDS and len(token) > 2:
            result.append(lemmatize_stemming(token))
    return result

def preprocess_for_train_data(text):
    return ' '.join(preprocess(text))

In [20]:
df = tt.select(['id', 'old_id', 'title', 'abstract']).toPandas()

In [21]:
%%time

with closing(multiprocessing.Pool(16)) as pool:
    ready_corpus = pool.map(preprocess_for_train_data, df['title'] + ' ' + df['abstract'])

2022-12-05 18:51:46,238 : INFO : Note: NumExpr detected 16 cores but "NUMEXPR_MAX_THREADS" not set, so enforcing safe limit of 8.
2022-12-05 18:51:46,239 : INFO : NumExpr defaulting to 8 threads.


CPU times: user 2.29 s, sys: 1.35 s, total: 3.65 s
Wall time: 2min 48s


In [22]:
train_data = pd.DataFrame(data=df[['id', 'old_id']])
train_data['prep_text'] = ready_corpus

train_data.to_csv(os.path.join(RESULT_FOLDER, 'train_data.csv'), index=False)

In [26]:
if spark is not None:
    spark.stop()
spark = None
train_data = None
gc.collect()

48

In [27]:
train_data = pd.read_csv('train_data.csv')

In [28]:
%%time

def split_text(text):
    return text.split(' ')

with closing(multiprocessing.Pool(16)) as pool:
    ready_corpus = pool.map(split_text, train_data['prep_text'])

CPU times: user 13.7 s, sys: 3.52 s, total: 17.2 s
Wall time: 17.5 s


In [29]:
train_data = None
len(ready_corpus)
gc.collect()

20

In [30]:
dictionary = gensim.corpora.Dictionary(ready_corpus)

2022-12-05 19:02:15,007 : INFO : adding document #0 to Dictionary<0 unique tokens: []>
2022-12-05 19:02:15,814 : INFO : adding document #10000 to Dictionary<19889 unique tokens: ['adjac', 'approxim', 'assign', 'color', 'defin']...>
2022-12-05 19:02:16,565 : INFO : adding document #20000 to Dictionary<29587 unique tokens: ['adjac', 'approxim', 'assign', 'color', 'defin']...>
2022-12-05 19:02:17,314 : INFO : adding document #30000 to Dictionary<37615 unique tokens: ['adjac', 'approxim', 'assign', 'color', 'defin']...>
2022-12-05 19:02:18,064 : INFO : adding document #40000 to Dictionary<44919 unique tokens: ['adjac', 'approxim', 'assign', 'color', 'defin']...>
2022-12-05 19:02:18,809 : INFO : adding document #50000 to Dictionary<51474 unique tokens: ['adjac', 'approxim', 'assign', 'color', 'defin']...>
2022-12-05 19:02:19,554 : INFO : adding document #60000 to Dictionary<57728 unique tokens: ['adjac', 'approxim', 'assign', 'color', 'defin']...>
2022-12-05 19:02:20,303 : INFO : adding doc

2022-12-05 19:02:58,561 : INFO : adding document #570000 to Dictionary<234629 unique tokens: ['adjac', 'approxim', 'assign', 'color', 'defin']...>
2022-12-05 19:02:59,353 : INFO : adding document #580000 to Dictionary<237177 unique tokens: ['adjac', 'approxim', 'assign', 'color', 'defin']...>
2022-12-05 19:03:00,123 : INFO : adding document #590000 to Dictionary<239812 unique tokens: ['adjac', 'approxim', 'assign', 'color', 'defin']...>
2022-12-05 19:03:00,897 : INFO : adding document #600000 to Dictionary<242377 unique tokens: ['adjac', 'approxim', 'assign', 'color', 'defin']...>
2022-12-05 19:03:01,668 : INFO : adding document #610000 to Dictionary<244978 unique tokens: ['adjac', 'approxim', 'assign', 'color', 'defin']...>
2022-12-05 19:03:02,445 : INFO : adding document #620000 to Dictionary<247506 unique tokens: ['adjac', 'approxim', 'assign', 'color', 'defin']...>
2022-12-05 19:03:03,212 : INFO : adding document #630000 to Dictionary<250029 unique tokens: ['adjac', 'approxim', 'as

In [31]:
dictionary.filter_extremes(no_below=30, no_above=0.4, keep_n=35000)
len(dictionary)

2022-12-05 19:03:35,877 : INFO : discarding 325280 tokens: [('paper', 579195), ('base', 485673), ('gouraud', 17), ('amazonia', 13), ('theglob', 13), ('theinterest', 7), ('propos', 426119), ('spir', 17), ('straightfor', 11), ('shruti', 7)]...
2022-12-05 19:03:35,877 : INFO : keeping 17941 tokens which were in no less than 30 and no more than 419212 (=40.0%) documents
2022-12-05 19:03:35,991 : INFO : resulting dictionary: Dictionary<17941 unique tokens: ['adjac', 'approxim', 'assign', 'color', 'defin']...>


17941

In [32]:
dictionary.save(os.path.join(RESULT_FOLDER, 'dictionary'))

2022-12-05 19:03:36,034 : INFO : Dictionary lifecycle event {'fname_or_handle': '/home/denis/dshibitov/courses/made/project_1/results/lda_model_3/dictionary', 'separately': 'None', 'sep_limit': 10485760, 'ignore': frozenset(), 'datetime': '2022-12-05T19:03:36.034476', 'gensim': '4.2.0', 'python': '3.7.9 (default, Aug 31 2020, 12:42:55) \n[GCC 7.3.0]', 'platform': 'Linux-5.4.0-135-generic-x86_64-with-debian-buster-sid', 'event': 'saving'}
2022-12-05 19:03:36,041 : INFO : saved /home/denis/dshibitov/courses/made/project_1/results/lda_model_3/dictionary


In [33]:
%%time

with closing(multiprocessing.Pool(16)) as pool:
    bow_corpus = pool.map(dictionary.doc2bow, ready_corpus)

CPU times: user 26.1 s, sys: 5.96 s, total: 32.1 s
Wall time: 32.3 s


In [34]:
with open(os.path.join(RESULT_FOLDER, 'bow_corpus.pkl'), 'wb') as file:
    pickle.dump(bow_corpus, file, protocol=pickle.HIGHEST_PROTOCOL)

ready_corpus = None

gc.collect()

20

In [45]:
with open(os.path.join(RESULT_FOLDER, 'bow_corpus.pkl'), 'rb') as file:
    bow_corpus = pickle.load(file)

In [35]:
%%time

tfidf = models.TfidfModel(bow_corpus)
corpus_tfidf = tfidf[bow_corpus]

2022-12-05 19:04:26,961 : INFO : collecting document frequencies
2022-12-05 19:04:26,962 : INFO : PROGRESS: processing document #0
2022-12-05 19:04:27,038 : INFO : PROGRESS: processing document #10000
2022-12-05 19:04:27,113 : INFO : PROGRESS: processing document #20000
2022-12-05 19:04:27,183 : INFO : PROGRESS: processing document #30000
2022-12-05 19:04:27,251 : INFO : PROGRESS: processing document #40000
2022-12-05 19:04:27,318 : INFO : PROGRESS: processing document #50000
2022-12-05 19:04:27,385 : INFO : PROGRESS: processing document #60000
2022-12-05 19:04:27,453 : INFO : PROGRESS: processing document #70000
2022-12-05 19:04:27,521 : INFO : PROGRESS: processing document #80000
2022-12-05 19:04:27,589 : INFO : PROGRESS: processing document #90000
2022-12-05 19:04:27,656 : INFO : PROGRESS: processing document #100000
2022-12-05 19:04:27,723 : INFO : PROGRESS: processing document #110000
2022-12-05 19:04:27,795 : INFO : PROGRESS: processing document #120000
2022-12-05 19:04:27,862 : 

CPU times: user 7.19 s, sys: 35.7 ms, total: 7.22 s
Wall time: 7.2 s


In [36]:
with open(os.path.join(RESULT_FOLDER, 'corpus_tfidf.pkl'), 'wb') as file:
    pickle.dump(corpus_tfidf, file, protocol=pickle.HIGHEST_PROTOCOL)

In [37]:
bow_corpus = None
gc.collect()

20

In [47]:
corpus_tfidf = None
lda_model = None
gc.collect()

20

In [48]:
%%time

a = dictionary[0]

# lda_model = gensim.models.LdaModel(
#     random_state=42,
#     corpus=corpus_tfidf,
#     id2word=dictionary.id2token,
#     chunksize=5000,
#     alpha='auto',
#     eta='auto',
#     iterations=75,
#     num_topics=100,
#     passes=10,
#     eval_every=30000
# )


lda_model = gensim.models.LdaModel(
    random_state=42,
    corpus=bow_corpus,
    id2word=dictionary.id2token,
    chunksize=5000,
    alpha='auto',
    eta='auto',
    iterations=75,
    num_topics=100,
    passes=10,
    eval_every=30000
)

2022-12-05 20:10:48,362 : INFO : using autotuned alpha, starting with [0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01, 0.01]
2022-12-05 20:10:48,365 : INFO : using serial LDA version on this node
2022-12-05 20:10:48,509 : INFO : running online (multi-pass) LDA training, 100 topics, 10 passes over the supplied corpus of 1048031 documents, updating model once every 5000 documents, evaluating perplexity every 1048031 documents, iterating 75x with a conv

2022-12-05 20:11:02,663 : INFO : topic #21 (0.010): 0.048*"servic" + 0.019*"model" + 0.016*"applic" + 0.013*"approach" + 0.011*"present" + 0.011*"comput" + 0.010*"cloud" + 0.010*"manag" + 0.009*"user" + 0.009*"requir"
2022-12-05 20:11:02,664 : INFO : topic #35 (0.010): 0.055*"featur" + 0.020*"method" + 0.019*"detect" + 0.017*"video" + 0.016*"extract" + 0.016*"object" + 0.015*"classif" + 0.015*"approach" + 0.014*"learn" + 0.011*"imag"
2022-12-05 20:11:02,665 : INFO : topic #25 (0.010): 0.061*"algorithm" + 0.025*"data" + 0.023*"method" + 0.013*"estim" + 0.012*"comput" + 0.012*"track" + 0.011*"result" + 0.011*"cluster" + 0.010*"point" + 0.009*"time"
2022-12-05 20:11:02,666 : INFO : topic diff=0.191926, rho=0.577350
2022-12-05 20:11:02,741 : INFO : PROGRESS: pass 0, at document #20000/1048031
2022-12-05 20:11:06,137 : INFO : optimized alpha [0.009686809, 0.0099688005, 0.009930327, 0.009954149, 0.009941342, 0.009955414, 0.009878802, 0.009659137, 0.009723836, 0.009769834, 0.010235713, 0.0099

2022-12-05 20:11:12,826 : INFO : topic #80 (0.011): 0.060*"problem" + 0.056*"optim" + 0.053*"algorithm" + 0.036*"search" + 0.024*"constraint" + 0.022*"solut" + 0.014*"solv" + 0.013*"object" + 0.012*"method" + 0.012*"genet"
2022-12-05 20:11:12,827 : INFO : topic #35 (0.011): 0.068*"featur" + 0.029*"classif" + 0.025*"method" + 0.022*"extract" + 0.021*"detect" + 0.020*"video" + 0.017*"learn" + 0.016*"classifi" + 0.016*"approach" + 0.015*"object"
2022-12-05 20:11:12,829 : INFO : topic diff=0.098436, rho=0.408248
2022-12-05 20:11:12,912 : INFO : PROGRESS: pass 0, at document #35000/1048031
2022-12-05 20:11:15,734 : INFO : optimized alpha [0.009846373, 0.010485805, 0.010218013, 0.010364872, 0.010529867, 0.010330784, 0.010170173, 0.009783627, 0.009710348, 0.009984121, 0.010926316, 0.010204028, 0.010222289, 0.010283475, 0.010394302, 0.010847739, 0.010841455, 0.010262195, 0.010899163, 0.010393705, 0.0112264715, 0.011326542, 0.011526076, 0.010190259, 0.010414272, 0.01142947, 0.009869419, 0.01025

2022-12-05 20:11:21,668 : INFO : topic #80 (0.013): 0.071*"problem" + 0.067*"optim" + 0.054*"algorithm" + 0.032*"search" + 0.025*"solut" + 0.023*"constraint" + 0.018*"solv" + 0.013*"heurist" + 0.012*"object" + 0.012*"method"
2022-12-05 20:11:21,670 : INFO : topic diff=0.088753, rho=0.333333
2022-12-05 20:11:21,745 : INFO : PROGRESS: pass 0, at document #50000/1048031
2022-12-05 20:11:24,349 : INFO : optimized alpha [0.010077006, 0.011098653, 0.010656187, 0.010830518, 0.011388069, 0.010824552, 0.010473178, 0.009962142, 0.009792546, 0.010279792, 0.011570461, 0.010539487, 0.010559376, 0.010723896, 0.011042105, 0.011673407, 0.011354503, 0.010804872, 0.011625013, 0.010868073, 0.012226512, 0.012056397, 0.012534498, 0.010574713, 0.010899304, 0.012233172, 0.0101989005, 0.010745492, 0.010643794, 0.00997832, 0.01053952, 0.011064631, 0.01034796, 0.010398854, 0.01065852, 0.012796159, 0.010715017, 0.010494319, 0.011144374, 0.010825449, 0.010452882, 0.011380898, 0.010347081, 0.0107130185, 0.01112878

2022-12-05 20:11:29,923 : INFO : topic diff=0.096129, rho=0.288675
2022-12-05 20:11:29,998 : INFO : PROGRESS: pass 0, at document #65000/1048031
2022-12-05 20:11:32,435 : INFO : optimized alpha [0.010301612, 0.011755136, 0.011182595, 0.011373922, 0.012380176, 0.011403397, 0.0107597755, 0.010129549, 0.009945251, 0.01066226, 0.012164988, 0.010921927, 0.010853601, 0.011186658, 0.011677985, 0.012652994, 0.011842582, 0.011450688, 0.012422751, 0.011371421, 0.01317861, 0.012816174, 0.013545983, 0.011045947, 0.011427229, 0.013190808, 0.0105690025, 0.011263696, 0.011287246, 0.010184638, 0.010978929, 0.0116389375, 0.010697515, 0.010748018, 0.011064207, 0.013744025, 0.011177244, 0.010948477, 0.011847581, 0.011378606, 0.011053753, 0.011830853, 0.010630346, 0.011196842, 0.011658786, 0.011012298, 0.011043205, 0.011831335, 0.010961378, 0.011019855, 0.011680724, 0.011980722, 0.011016559, 0.011691641, 0.010652763, 0.010796357, 0.010419924, 0.011275094, 0.013125345, 0.010905768, 0.010089874, 0.011839347

...

2022-12-05 21:10:54,591 : INFO : merging changes from 5000 documents into a model of 1048031 documents
2022-12-05 21:10:54,661 : INFO : topic #8 (0.058): 0.101*"branch" + 0.060*"predictor" + 0.050*"invert" + 0.045*"stress" + 0.034*"indirect" + 0.028*"imprecis" + 0.027*"shoot" + 0.027*"percentag" + 0.023*"secreci" + 0.023*"coalit"
2022-12-05 21:10:54,662 : INFO : topic #0 (0.058): 0.121*"multicast" + 0.064*"aid" + 0.050*"cut" + 0.045*"port" + 0.038*"offlin" + 0.036*"immun" + 0.034*"impair" + 0.031*"leader" + 0.031*"dispers" + 0.027*"hyper"
2022-12-05 21:10:54,663 : INFO : topic #38 (0.654): 0.069*"framework" + 0.064*"oper" + 0.056*"type" + 0.042*"defin" + 0.041*"construct" + 0.038*"concept" + 0.036*"logic" + 0.034*"represent" + 0.029*"specif" + 0.026*"formal"
2022-12-05 21:10:54,664 : INFO : topic #25 (2.299): 0.056*"result" + 0.053*"algorithm" + 0.053*"perform" + 0.029*"techniqu" + 0.027*"effici" + 0.027*"improv" + 0.024*"high" + 0.023*"effect" + 0.022*"compar" + 0.017*"order"
2022-12-

2022-12-05 21:10:58,930 : INFO : topic #38 (0.655): 0.069*"framework" + 0.064*"oper" + 0.056*"type" + 0.042*"defin" + 0.040*"construct" + 0.039*"concept" + 0.036*"logic" + 0.034*"represent" + 0.028*"specif" + 0.026*"formal"
2022-12-05 21:10:58,931 : INFO : topic #25 (2.299): 0.056*"result" + 0.054*"algorithm" + 0.052*"perform" + 0.029*"techniqu" + 0.027*"effici" + 0.027*"improv" + 0.024*"high" + 0.023*"effect" + 0.022*"compar" + 0.017*"order"
2022-12-05 21:10:58,932 : INFO : topic #17 (3.391): 0.033*"approach" + 0.023*"system" + 0.023*"applic" + 0.022*"differ" + 0.022*"present" + 0.021*"analysi" + 0.021*"provid" + 0.019*"studi" + 0.014*"work" + 0.014*"evalu"
2022-12-05 21:10:58,935 : INFO : topic diff=0.002649, rho=0.067480
2022-12-05 21:10:59,012 : INFO : PROGRESS: pass 9, at document #1015000/1048031
2022-12-05 21:11:00,212 : INFO : optimized alpha [0.058156066, 0.13697942, 0.10479154, 0.10492316, 0.22908132, 0.08345595, 0.070807375, 0.16946247, 0.05759457, 0.12016218, 0.096801825, 0

2022-12-05 21:11:03,277 : INFO : topic #17 (3.393): 0.033*"approach" + 0.023*"system" + 0.023*"applic" + 0.023*"differ" + 0.023*"present" + 0.021*"analysi" + 0.021*"provid" + 0.019*"studi" + 0.014*"work" + 0.013*"evalu"
2022-12-05 21:11:03,281 : INFO : topic diff=0.002886, rho=0.067480
2022-12-05 21:11:03,356 : INFO : PROGRESS: pass 9, at document #1030000/1048031
2022-12-05 21:11:04,595 : INFO : optimized alpha [0.05820194, 0.13695247, 0.10487388, 0.104922734, 0.22901268, 0.0834616, 0.0708443, 0.16959669, 0.057622902, 0.12021761, 0.09684618, 0.10580869, 0.09357965, 0.10385059, 0.12572268, 0.28531593, 0.10571299, 3.3934937, 0.16131973, 0.13762268, 0.19565609, 0.1694251, 0.23312962, 0.085403346, 0.09312656, 2.2996027, 0.076663144, 0.110204406, 0.25841674, 0.13981035, 0.11001215, 0.12244853, 0.09940465, 0.08108842, 0.098563045, 0.16950135, 0.18004148, 0.32785654, 0.65653217, 0.12364576, 0.36579052, 0.09655352, 0.095793426, 0.12592427, 0.10713698, 0.15568933, 0.1118614, 0.15839903, 0.0970

2022-12-05 21:11:09,066 : INFO : merging changes from 5000 documents into a model of 1048031 documents
2022-12-05 21:11:09,138 : INFO : topic #8 (0.058): 0.104*"branch" + 0.057*"predictor" + 0.050*"invert" + 0.045*"stress" + 0.035*"indirect" + 0.028*"percentag" + 0.027*"shoot" + 0.025*"imprecis" + 0.024*"coalit" + 0.023*"secreci"
2022-12-05 21:11:09,139 : INFO : topic #0 (0.058): 0.123*"multicast" + 0.063*"aid" + 0.050*"cut" + 0.040*"port" + 0.036*"offlin" + 0.034*"immun" + 0.033*"impair" + 0.032*"leader" + 0.029*"dispers" + 0.028*"hyper"
2022-12-05 21:11:09,140 : INFO : topic #38 (0.656): 0.069*"framework" + 0.065*"oper" + 0.057*"type" + 0.042*"defin" + 0.040*"construct" + 0.038*"concept" + 0.036*"logic" + 0.034*"represent" + 0.028*"specif" + 0.026*"formal"
2022-12-05 21:11:09,141 : INFO : topic #25 (2.301): 0.056*"result" + 0.053*"algorithm" + 0.052*"perform" + 0.029*"techniqu" + 0.027*"effici" + 0.027*"improv" + 0.024*"high" + 0.023*"effect" + 0.022*"compar" + 0.017*"order"
2022-12-

CPU times: user 1h 24s, sys: 3.31 s, total: 1h 27s
Wall time: 1h 23s


In [52]:
model_datapath = datapath(os.path.join(RESULT_FOLDER, 'model.lda'))
lda_model.save(model_datapath)

2022-12-05 22:23:30,095 : INFO : LdaState lifecycle event {'fname_or_handle': '/home/denis/dshibitov/courses/made/project_1/results/lda_model_3/model.lda.state', 'separately': 'None', 'sep_limit': 10485760, 'ignore': frozenset(), 'datetime': '2022-12-05T22:23:30.095535', 'gensim': '4.2.0', 'python': '3.7.9 (default, Aug 31 2020, 12:42:55) \n[GCC 7.3.0]', 'platform': 'Linux-5.4.0-135-generic-x86_64-with-debian-buster-sid', 'event': 'saving'}
2022-12-05 22:23:30,106 : INFO : saved /home/denis/dshibitov/courses/made/project_1/results/lda_model_3/model.lda.state
2022-12-05 22:23:30,111 : INFO : LdaModel lifecycle event {'fname_or_handle': '/home/denis/dshibitov/courses/made/project_1/results/lda_model_3/model.lda', 'separately': "['expElogbeta', 'sstats']", 'sep_limit': 10485760, 'ignore': ['state', 'id2word', 'dispatcher'], 'datetime': '2022-12-05T22:23:30.111343', 'gensim': '4.2.0', 'python': '3.7.9 (default, Aug 31 2020, 12:42:55) \n[GCC 7.3.0]', 'platform': 'Linux-5.4.0-135-generic-x86

In [50]:
lda_model.inference([bow_corpus[0], bow_corpus[3000], bow_corpus[918000]])

(array([[ 0.05819253,  0.13730535,  0.10496555,  0.10481291,  0.23047173,
          0.08349117,  0.07080969,  0.16951951,  0.05758787,  2.1202097 ,
          0.09681988,  0.10593871,  0.09356076,  0.10393351,  0.12590158,
          5.4043565 ,  0.10578316,  5.8296995 ,  0.16135135,  0.13818787,
          0.19715616,  0.16956039,  0.23307258,  0.08529364,  0.09315009,
          3.1821594 ,  0.07674135,  0.11016265,  0.25859746,  0.13985139,
          0.11006789,  0.12234885,  0.09955401,  0.08110268,  0.09855976,
          0.16957277,  4.1486287 ,  0.32717055,  1.658463  ,  0.12357392,
          1.210351  ,  0.09666763,  0.09591718,  0.12602174,  3.1072025 ,
          0.15542832,  0.11184134,  0.15878344,  0.09709845,  0.0905287 ,
          0.22906308,  0.16721757,  0.22439033,  0.16601585,  0.0941264 ,
          0.10988583,  0.07271364,  0.10709237,  0.11827135,  0.14158653,
          0.13023436,  0.1618789 ,  0.17945893,  0.10181341,  3.1033642 ,
          0.20310147,  0.10568092,  0.

In [51]:
lda_model[bow_corpus[0]], lda_model[bow_corpus[3000]], lda_model[bow_corpus[918000]]

([(9, 0.030162675),
  (15, 0.076883785),
  (17, 0.08293581),
  (25, 0.04527034),
  (36, 0.05901951),
  (38, 0.023593698),
  (40, 0.017209964),
  (44, 0.0442039),
  (64, 0.0441493),
  (68, 0.14594765),
  (73, 0.13398758),
  (80, 0.07394383),
  (87, 0.04018497),
  (99, 0.016275236)],
 [(11, 0.02367672),
  (17, 0.14212513),
  (20, 0.05913884),
  (25, 0.11404163),
  (28, 0.062035676),
  (36, 0.018239783),
  (46, 0.062535875),
  (52, 0.03540624),
  (60, 0.018332615),
  (62, 0.19428326),
  (92, 0.11406944),
  (96, 0.013841509)],
 [(7, 0.010327815),
  (10, 0.010788838),
  (15, 0.08101724),
  (17, 0.10769907),
  (25, 0.11670834),
  (27, 0.018632352),
  (36, 0.028083695),
  (37, 0.011938982),
  (38, 0.026161993),
  (45, 0.010202703),
  (52, 0.09026567),
  (62, 0.03206654),
  (75, 0.010250503),
  (77, 0.028793404),
  (80, 0.21654391),
  (83, 0.010188619),
  (87, 0.025951082),
  (90, 0.019150505),
  (95, 0.012260393),
  (98, 0.0187433)])

In [53]:
corpus_tfidf[0]

TypeError: 'NoneType' object is not subscriptable

In [59]:
matrix_similarity = MatrixSimilarity(lda_model[bow_corpus], num_best=1000, num_features=100)

2022-12-05 22:43:20,247 : INFO : creating matrix with 1048031 documents and 100 features


In [60]:
matrix_similarity.save(os.path.join(RESULT_FOLDER, 'matrix_similarity'))

2022-12-05 22:50:44,235 : INFO : MatrixSimilarity lifecycle event {'fname_or_handle': '/home/denis/dshibitov/courses/made/project_1/results/lda_model_3/matrix_similarity', 'separately': 'None', 'sep_limit': 10485760, 'ignore': frozenset(), 'datetime': '2022-12-05T22:50:44.235396', 'gensim': '4.2.0', 'python': '3.7.9 (default, Aug 31 2020, 12:42:55) \n[GCC 7.3.0]', 'platform': 'Linux-5.4.0-135-generic-x86_64-with-debian-buster-sid', 'event': 'saving'}
2022-12-05 22:50:44,236 : INFO : storing np array 'index' to /home/denis/dshibitov/courses/made/project_1/results/lda_model_3/matrix_similarity.index.npy
2022-12-05 22:50:44,434 : INFO : saved /home/denis/dshibitov/courses/made/project_1/results/lda_model_3/matrix_similarity


### Примеры рекомендаций

In [34]:
ar = ArticleRecommendation('/home/denis/dshibitov/courses/made/project_1/results/lda_model_3')

2022-12-06 21:54:03,708 : INFO : loading LdaModel object from /home/denis/dshibitov/courses/made/project_1/results/lda_model_3/model.lda
2022-12-06 21:54:03,710 : INFO : loading expElogbeta from /home/denis/dshibitov/courses/made/project_1/results/lda_model_3/model.lda.expElogbeta.npy with mmap=None
2022-12-06 21:54:03,711 : INFO : setting ignored attribute state to None
2022-12-06 21:54:03,712 : INFO : setting ignored attribute id2word to None
2022-12-06 21:54:03,712 : INFO : setting ignored attribute dispatcher to None
2022-12-06 21:54:03,713 : INFO : LdaModel lifecycle event {'fname': '/home/denis/dshibitov/courses/made/project_1/results/lda_model_3/model.lda', 'datetime': '2022-12-06T21:54:03.713010', 'gensim': '4.2.0', 'python': '3.7.9 (default, Aug 31 2020, 12:42:55) \n[GCC 7.3.0]', 'platform': 'Linux-5.4.0-135-generic-x86_64-with-debian-buster-sid', 'event': 'loaded'}
2022-12-06 21:54:03,713 : INFO : loading LdaState object from /home/denis/dshibitov/courses/made/project_1/resul

In [9]:
te = tt.select(['id', 'title', 'abstract']).sample(withReplacement=False, fraction=0.99, seed=42).toPandas()

In [12]:
ids = [random.randint(0, len(te)) for _ in range(10)]
ids

[992579, 384889, 946421, 168765, 285179, 507212, 781341, 4724, 604232, 123675]

In [20]:
rr

[738152, 767307, 218838, 783631, 379702]

In [19]:
for i in ids[:10]:
    row = te.iloc[i]
    print(f'{row["id"]}. =============================')
    print(row['title'])
    print(row['abstract'])
    
    recs = ar.get_recomendations(row['id'], count=5, skip=0)
    rr = recs
    print(recs)
    recs = [x for x in recs if x != row['id']]
    for _i, rec in enumerate(recs):
        found = te[te.id == rec]
        if len(found) > 0:
            t = found.iloc[0]
            print(f'rec {_i} {rec}')
            print(t['title'])
            print(t['abstract'])
            print('----------------')
        else:
            print('no id in test')
    
    
    print('=============================')

344939. =============================
Mapping interleaving laws to parallel turbo and LDPC decoder architectures
For high-data-rate applications, the implementation of iterative turbo-like decoders requires the use of parallel architectures posing some collision-free constraints to the reading/writing process from/into the memory. This consideration applies to the two main classes of turbo-like codes, i.e., turbo codes and low-density parity-check (LDPC) codes. Contrary to the literature belief, we prove in this paper that there is no need for an ad hoc code design to meet the parallelism requirement, because, for any code and any choice of the scheduling of the reading/writing operations, there is a suitable mapping of the variables in the memory that grants a collision-free access. The proof is constructive, i.e., it gives an algorithm that obtains the desired collision-free mapping. The algorithm is applied to two simple examples, one for turbo codes and one for LDPC codes, to illus

[(0, (170518, 0.9999998211860657)), (1, (831162, 0.9544600248336792)), (2, (812362, 0.9521262049674988)), (3, (503953, 0.9505780935287476)), (4, (1028751, 0.9478127360343933))]
[344668, 849427, 559461, 9968, 749557]
rec 0 849427
Rapid accurate frequency estimation of multiple resolved exponentials in noise.
The estimation of the frequencies of the sum of multiple resolved exponentials in noise is an important problem due to its application in diverse areas from engineering to chemistry. Yet to date, no low cost Fourier-based algorithm has been successful at obtaining unbiased estimates that achieve the CramrRao lower bound (CRLB) over a wide range of signal-to-noise ratios. In this work, we achieve precisely this goal, proposing a fast yet accurate estimator that combines an iterative frequency-domain interpolation step with a leakage subtraction scheme. By analysing the asymptotic performance and the convergence behaviour of the estimator, we show that the estimate of each frequency c

[(0, (4768, 1.0)), (1, (320659, 0.9453800320625305)), (2, (392593, 0.9445635676383972)), (3, (915850, 0.9388559460639954)), (4, (408437, 0.93885338306427))]
[66976, 396748, 403064, 57245, 644294]
rec 0 396748
Issues in Adaptive Collaboration
In the modern world, adaptability is a key performance index for a group to be competitive. The use of well-designed computer tools by its members can help increase its adaptability. The purpose of Adaptive Collaboration (AC) is to obtain the optimal group performance, e.g., the maximum sum of the individual performances of group members in their positions for a concerned period of time. AC is a natural extension of Role-Based Collaboration (RBC). Our early model E-CARGO (Environments - Classes, Agents, Roles, Groups, and Objects) of RBC can become a fundamental model for AC. This paper points out the key issues facing AC researchers, analyzes the key factors related with adaptability, clarifies the AC process, and outlines some preliminary yet pro

## Examples 2

In [38]:
for i in ids[:10]:
    row = te.iloc[i]
    print('==============================================')
    print(f'Article id = {row["id"]}')
    print('==============================================')
    print(f'Title: {row["title"]}')
    print(f'Abstract: {row["abstract"]}')
    
    recs = ar.get_recommendations(row['id'], count=6, skip=0, keep_source=True)
    rr = recs
    print()
    print('Recomendations ids: ', recs)
#     recs = [x for x in recs if x != row['id']]
    print()
    
    for _i, rec in enumerate(recs):
        found = te[te.id == rec]
        if len(found) > 0:
            t = found.iloc[0]
            print(f'Recomendation {_i + 1}. id = {rec}')
            print(f'Title: {t["title"]}')
            print(f'Abstract: {t["abstract"]}')
            print('----------------')
        else:
            print('no id in test')
    
    
    print('=============================')
    print()
    print()
    print()
    print()

Article id = 344939
Title: Mapping interleaving laws to parallel turbo and LDPC decoder architectures
Abstract: For high-data-rate applications, the implementation of iterative turbo-like decoders requires the use of parallel architectures posing some collision-free constraints to the reading/writing process from/into the memory. This consideration applies to the two main classes of turbo-like codes, i.e., turbo codes and low-density parity-check (LDPC) codes. Contrary to the literature belief, we prove in this paper that there is no need for an ad hoc code design to meet the parallelism requirement, because, for any code and any choice of the scheduling of the reading/writing operations, there is a suitable mapping of the variables in the memory that grants a collision-free access. The proof is constructive, i.e., it gives an algorithm that obtains the desired collision-free mapping. The algorithm is applied to two simple examples, one for turbo codes and one for LDPC codes, to illust


Recomendations ids:  [344668, 849427, 559461, 9968, 749557, 470162]

Recomendation 1. id = 344668
Title: Sparse semi-parametric chirp estimation
Abstract: In this work, we present a method for estimating the parameters detailing an unknown number of linear chirp signals, using an iterative sparse reconstruction framework. The proposed method is initiated by a re-weighted Lasso approach, and then use an iterative relaxation-based refining step to allow for high resolution estimates. The resulting estimates are found to be statistically efficient, achieving the Cramér-Rao lower bound. Numerical simulations illustrate the achievable performance, offering a notable improvement as compared to other recent approaches.
----------------
Recomendation 2. id = 849427
Title: Rapid accurate frequency estimation of multiple resolved exponentials in noise.
Abstract: The estimation of the frequencies of the sum of multiple resolved exponentials in noise is an important problem due to its applicatio


Recomendations ids:  [66976, 396748, 403064, 57245, 644294, 510369]

Recomendation 1. id = 66976
Title: Individual differences and the conundrums of user-centered design: two experiments
Abstract: Individual differences between users of information systems can influence search performance. In user-centered design it is important to match users with system configurations that will optimize their performance. Two matching strategies were explored in the first experiment: the capitalization match, and the compensatory match. Findings suggest that a compensatory match is likely to be encountered more frequently in designing information systems. Having determined an optimal match between users and system configurations, it is necessary to find ways to ensure that users are guided to the appropriate configuration. The second experiment examined user selection of system configurations, and concluded that users do not act to optimize system configuration when they select features. This result